In [1]:
import pandas as pd 
import numpy as np
from sklearn.preprocessing import MinMaxScaler
import seaborn as sns

In [2]:
house_df = pd.read_csv('data/housing.csv')

In [3]:
house_df.shape

(20640, 10)

In [4]:
house_df.head()

longitude  latitude  housing_median_age  total_rooms  total_bedrooms  \
0    -122.23     37.88                41.0        880.0           129.0   
1    -122.22     37.86                21.0       7099.0          1106.0   
2    -122.24     37.85                52.0       1467.0           190.0   
3    -122.25     37.85                52.0       1274.0           235.0   
4    -122.25     37.85                52.0       1627.0           280.0   

   population  households  median_income  median_house_value ocean_proximity  
0       322.0       126.0         8.3252            452600.0        NEAR BAY  
1      2401.0      1138.0         8.3014            358500.0        NEAR BAY  
2       496.0       177.0         7.2574            352100.0        NEAR BAY  
3       558.0       219.0         5.6431            341300.0        NEAR BAY  
4       565.0       259.0         3.8462            342200.0        NEAR BAY

In [5]:
house_df.describe()

longitude      latitude  housing_median_age   total_rooms  \
count  20640.000000  20640.000000        20640.000000  20640.000000   
mean    -119.569704     35.631861           28.639486   2635.763081   
std        2.003532      2.135952           12.585558   2181.615252   
min     -124.350000     32.540000            1.000000      2.000000   
25%     -121.800000     33.930000           18.000000   1447.750000   
50%     -118.490000     34.260000           29.000000   2127.000000   
75%     -118.010000     37.710000           37.000000   3148.000000   
max     -114.310000     41.950000           52.000000  39320.000000   

       total_bedrooms    population    households  median_income  \
count    20433.000000  20640.000000  20640.000000   20640.000000   
mean       537.870553   1425.476744    499.539680       3.870671   
std        421.385070   1132.462122    382.329753       1.899822   
min          1.000000      3.000000      1.000000       0.499900   
25%        296.000000    787.000000    280.000000       2.563400   
50%        435.000000   1166.000000    409.000000       3.534800   
75%        647.000000   1725.000000    605.000000       4.743250   
max       6445.000000  35682.000000   6082.000000      15.000100   

       median_house_value  
count        20640.000000  
mean        206855.816909  
std         115395.615874  
min          14999.000000  
25%         119600.000000  
50%         179700.000000  
75%         264725.000000  
max         500001.000000

In [6]:
sum(house_df.duplicated())

0

In [7]:
house_df = house_df.dropna()

valeurs moyennes ecarts types / intervalle de confiance
statsmodel
intervalle de confiance => calcul des erreurs entre les données observer et données predites
MSe et RMSE
Catégoriser
Total rooms
Total bedrooms


In [8]:
np.unique(house_df['housing_median_age'])#Selection des valeurs catégorielles de housing_median_age

array([ 1.,  2.,  3.,  4.,  5.,  6.,  7.,  8.,  9., 10., 11., 12., 13.,
       14., 15., 16., 17., 18., 19., 20., 21., 22., 23., 24., 25., 26.,
       27., 28., 29., 30., 31., 32., 33., 34., 35., 36., 37., 38., 39.,
       40., 41., 42., 43., 44., 45., 46., 47., 48., 49., 50., 51., 52.])

Ocean Proximity encodage

In [9]:
house_df.loc[house_df['ocean_proximity'] == 'NEAR BAY', 'ocean_proximity'] = 1

In [10]:
house_df.loc[house_df['ocean_proximity'] == 'NEAR OCEAN', 'ocean_proximity'] = 2

In [11]:
house_df.loc[house_df['ocean_proximity'] == 'ISLAND', 'ocean_proximity'] = 3

In [12]:
house_df.loc[house_df['ocean_proximity'] == '<1H OCEAN', 'ocean_proximity'] = 4

In [13]:
house_df.loc[house_df['ocean_proximity'] == 'INLAND', 'ocean_proximity'] = 5

Median income

In [14]:
import pandas_profiling
from pandas_profiling.utils.cache import cache_file

In [15]:
report = house_df.profile_report(
    sort=None, html={"style": {"full_width": True}}, progress_bar=False
)
report

In [16]:
import pickle
from sklearn.model_selection import train_test_split

In [17]:
%%capture

house_df['total_rooms'] = house_df['total_rooms'] / house_df['households']
house_df['total_bedrooms'] = house_df['total_bedrooms'] / house_df['households']
house_df['population'] = house_df['population'] / house_df['households']

X = house_df[['housing_median_age','total_rooms','total_bedrooms','median_income', 'population', 'ocean_proximity']]
y = house_df["median_house_value"]

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

X_scaler = MinMaxScaler()
y_scaler = MinMaxScaler()

# Fit & transform the train split and just transform the test split
X_train_scaled = X_scaler.fit_transform(X_train)
X_test_scaled = X_scaler.transform(X_test)

y_train_scaled = y_scaler.fit_transform(np.array(y_train).reshape(-1, 1))
y_test_scaled = y_scaler.transform(np.array(y_test).reshape(-1, 1))

# Final scaler on entire dataset X, y
X_scaler = MinMaxScaler()
y_scaler = MinMaxScaler()
X_scaler.fit_transform(X)
y_scaler.fit_transform(np.array(y).reshape((-1, 1)))

In [ ]:
# Save X, y and the scaler for later use

# X,y Scaler

with open('data/X_scaler.pickle', 'wb') as handle:
    pickle.dump(X_scaler, handle, protocol=pickle.HIGHEST_PROTOCOL)
with open('data/y_scaler.pickle', 'wb') as handle:
    pickle.dump(y_scaler, handle, protocol=pickle.HIGHEST_PROTOCOL)

# Train
with open('data/X_train_scaled.pickle', 'wb') as handle:
    pickle.dump(X_train_scaled, handle, protocol=pickle.HIGHEST_PROTOCOL)
with open('data/y_train_scaled.pickle', 'wb') as handle:
    pickle.dump(y_train_scaled, handle, protocol=pickle.HIGHEST_PROTOCOL)

# Test
with open('data/X_test_scaled.pickle', 'wb') as handle:
    pickle.dump(X_test_scaled, handle, protocol=pickle.HIGHEST_PROTOCOL)
with open('data/y_test_scaled.pickle', 'wb') as handle:
    pickle.dump(y_test_scaled, handle, protocol=pickle.HIGHEST_PROTOCOL)